Carregando Pacotes

In [2]:
from OSMPythonTools.overpass import Overpass
import geojson
import geopandas as gpd
import pandas as pd
import folium

Fazendo a chamada na API Overpass

In [3]:
xmin = -47.718776741  # Longitude mínima
ymin = -22.779978939  # Latitude mínima
xmax = -47.545732951  # Longitude máxima
ymax = -22.686138463  # Latitude máxima
bbox = f"{ymin},{xmin},{ymax},{xmax}"

overpass = Overpass()

# Consulta
overpass_query = f"""
(
  way["highway"]({bbox});
);
out geom;
"""
result = overpass.query(overpass_query)

Convertendo a Resposta em GeoJSON/Geodataframe e gravando o arquvivo em Shapefile

In [ ]:
# Criar um GeoJSON
features = []

for element in result.elements():
    properties = {
        'id': element.id(),
        'tags': element.tags()
    }

    feature = geojson.Feature(geometry=element.geometry(), properties=properties)

    features.append(feature)


feature_collection = geojson.FeatureCollection(features)

# Converter GeoJSON para GeoDataFrame
gdf = gpd.GeoDataFrame.from_features(feature_collection['features'])

# Expandir as tags em colunas
tags = gdf['tags'].apply(pd.Series)
gdf = pd.concat([gdf.drop(['tags'], axis=1), tags], axis=1)

# Salvar como Shapefile
gdf.set_crs(epsg=4326, inplace=True)
gdf.to_file('output/OSM_output.shp', driver='ESRI Shapefile')

Visualizando os dados no mapa

In [5]:
def style_function(feature):
    if feature['properties']['tags']['highway'] == 'primary':
        return {'color': '#ff0000'}  # vermelho para rodovias primárias
    elif feature['properties']['tags']['highway'] == 'secondary':
        return {'color': '#0000ff'}  # azul para rodovias secundárias
    else:
        return {'color': '#a0978d'}  # cinza para todos os outros tipos de rodovias
    
# Cria o mapa centralizado na média das latitudes e longitudes
mapa = folium.Map(location=[(ymin+ymax)/2, (xmin+xmax)/2], zoom_start=13)

#Adiciona o GeoJSON ao mapa
folium.GeoJson(feature_collection, style_function=style_function).add_to(mapa)

mapa